In [1]:
import requests
import json
import pandas as pd
import plotly.express as px
from datetime import datetime
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import sys

In [2]:
# Dokumenteneinstellung
# DataFrame Options
np.set_printoptions(threshold=sys.maxsize)
pd.set_option("display.max_rows", 50)
pd.set_option("display.max_columns", 50)
pd.set_option("display.width", 1000)

In [3]:
# Base URL for the OpenSenseMap API
base_url = "https://api.opensensemap.org/boxes"
# SenseBox ID
senseBoxId = "6645db6eeb5aad0007a6e4b6"
# List of Sensor IDs
sensorIds = [
    "6645db6eeb5aad0007a6e4b7",  
    "6645db6eeb5aad0007a6e4b8",
    "6645db6eeb5aad0007a6e4b9",
    "6645db6eeb5aad0007a6e4ba"
]

# Parameters
params = {
    'format': 'json',            
    'from-date': '2024-05-16T19:00:00Z',
    #'to-date': datetime.now(),
    'download': 'true',          
    'outliers': 'mark',          
    'outlier-window': 15,        
    'delimiter': 'comma'         
}


all_data = []


for sensorId in sensorIds:
    endpoint = f'{base_url}/{senseBoxId}/data/{sensorId}'
    response = requests.get(endpoint, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        # Add sensor ID to each measurement
        for measurement in data:
            measurement['Id'] = sensorId
            # Check for outliers and add an 'outlier' column
            if 'outlier' in measurement:
                measurement['outlier'] = measurement['outlier']
            else:
                measurement['outlier'] = None  # If no outlier info, set as None
        all_data.extend(data)
    else:
        print(f'Error retrieving data for sensor {sensorId}: {response.status_code}')


sense_df = pd.DataFrame(all_data)
sense_df

location                 createdAt   value  isOutlier                        Id outlier
0      [8.410042, 49.001548]  2024-05-27T13:41:51.083Z   24.08      False  6645db6eeb5aad0007a6e4b7    None
1      [8.410042, 49.001548]  2024-05-27T13:40:50.156Z   24.02      False  6645db6eeb5aad0007a6e4b7    None
2      [8.410042, 49.001548]  2024-05-27T13:39:49.937Z   24.18      False  6645db6eeb5aad0007a6e4b7    None
3      [8.410042, 49.001548]  2024-05-27T13:38:49.791Z   24.24      False  6645db6eeb5aad0007a6e4b7    None
4      [8.410042, 49.001548]  2024-05-27T13:37:49.668Z   24.30      False  6645db6eeb5aad0007a6e4b7    None
...                      ...                       ...     ...        ...                       ...     ...
39995  [8.410042, 49.001548]  2024-05-20T14:18:29.029Z  219.38       True  6645db6eeb5aad0007a6e4ba    None
39996  [8.410042, 49.001548]  2024-05-20T14:17:28.871Z  213.75      False  6645db6eeb5aad0007a6e4ba    None
39997  [8.410042, 49.001548]  2024-05-20T14:16:28.843Z  213.75      False  6645db6eeb5aad0007a6e4ba    None
39998  [8.410042, 49.001548]  2024-05-20T14:15:28.666Z  213.75      False  6645db6eeb5aad0007a6e4ba    None
39999  [8.410042, 49.001548]  2024-05-20T14:14:28.566Z  219.38      False  6645db6eeb5aad0007a6e4ba    None

[40000 rows x 6 columns]

In [4]:
sense_df['createdAt'] = pd.to_datetime(sense_df['createdAt'])

sensor_info = {
    '6645db6eeb5aad0007a6e4b7': {'name': 'Temperatur', 'unit': '°C'},
    '6645db6eeb5aad0007a6e4b8': {'name': 'rel. Luftfeuchte', 'unit': '%'},
    '6645db6eeb5aad0007a6e4b9': {'name': 'Luftdruck', 'unit': 'hPa'},
    '6645db6eeb5aad0007a6e4ba': {'name': 'UV-Intensität', 'unit': 'μW/cm²'},
}

sense_df['sensor_name'] = sense_df['Id'].map(lambda x: sensor_info[x]['name'])
sense_df['unit'] = sense_df['Id'].map(lambda x: sensor_info[x]['unit'])

In [5]:
sense_df.dtypes

location                    object
createdAt      datetime64[ns, UTC]
value                       object
isOutlier                     bool
Id                          object
outlier                     object
sensor_name                 object
unit                        object
dtype: object

# Outlier

In [6]:
outliers_df = sense_df[sense_df['isOutlier'] == True]
outliers_df

location                        createdAt   value  isOutlier                        Id outlier    sensor_name    unit
15     [8.410042, 49.001548] 2024-05-27 13:26:48.321000+00:00   23.98       True  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
16     [8.410042, 49.001548] 2024-05-27 13:25:48.262000+00:00   23.80       True  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
17     [8.410042, 49.001548] 2024-05-27 13:24:48.052000+00:00   23.87       True  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
38     [8.410042, 49.001548] 2024-05-27 13:03:45.934000+00:00   24.31       True  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
39     [8.410042, 49.001548] 2024-05-27 13:02:45.813000+00:00   24.22       True  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
...                      ...                              ...     ...        ...                       ...     ...            ...     ...
39985  [8.410042, 49.001548] 2024-05-20 14:28:30.207000+00:00  191.25       True  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39992  [8.410042, 49.001548] 2024-05-20 14:21:29.298000+00:00  219.38       True  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39993  [8.410042, 49.001548] 2024-05-20 14:20:29.267000+00:00  219.38       True  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39994  [8.410042, 49.001548] 2024-05-20 14:19:29.207000+00:00  225.00       True  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39995  [8.410042, 49.001548] 2024-05-20 14:18:29.029000+00:00  219.38       True  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²

[8271 rows x 8 columns]

In [7]:
num_outliers = sense_df['isOutlier'].sum()
print("Anzahl der Outlier im DataFrame:", num_outliers)

Anzahl der Outlier im DataFrame: 8271


# Anzahl Messwerte

In [8]:
num_measurements = sense_df.shape[0]
print("Anzahl der Messwerte im DataFrame:", num_measurements)

Anzahl der Messwerte im DataFrame: 40000


In [9]:
# Gesamtzahl der Messwerte
total_measurements = sense_df.shape[0]
# Prozentsatz der Outliers
percent_outliers = (num_outliers / total_measurements) * 100

print(f"Prozentsatz der Outliers im DataFrame: {percent_outliers:.2f}%")

Prozentsatz der Outliers im DataFrame: 20.68%


# Bereinigter Datensatz

In [10]:
df = sense_df[sense_df['isOutlier'] == False]
df

location                        createdAt   value  isOutlier                        Id outlier    sensor_name    unit
0      [8.410042, 49.001548] 2024-05-27 13:41:51.083000+00:00   24.08      False  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
1      [8.410042, 49.001548] 2024-05-27 13:40:50.156000+00:00   24.02      False  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
2      [8.410042, 49.001548] 2024-05-27 13:39:49.937000+00:00   24.18      False  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
3      [8.410042, 49.001548] 2024-05-27 13:38:49.791000+00:00   24.24      False  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
4      [8.410042, 49.001548] 2024-05-27 13:37:49.668000+00:00   24.30      False  6645db6eeb5aad0007a6e4b7    None     Temperatur      °C
...                      ...                              ...     ...        ...                       ...     ...            ...     ...
39991  [8.410042, 49.001548] 2024-05-20 14:22:29.468000+00:00  208.12      False  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39996  [8.410042, 49.001548] 2024-05-20 14:17:28.871000+00:00  213.75      False  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39997  [8.410042, 49.001548] 2024-05-20 14:16:28.843000+00:00  213.75      False  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39998  [8.410042, 49.001548] 2024-05-20 14:15:28.666000+00:00  213.75      False  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²
39999  [8.410042, 49.001548] 2024-05-20 14:14:28.566000+00:00  219.38      False  6645db6eeb5aad0007a6e4ba    None  UV-Intensität  μW/cm²

[31729 rows x 8 columns]

# Daten in eine Zeile schreiben 

In [11]:
opensense_df = df.pivot_table(index='createdAt', columns='sensor_name', values='value').reset_index()

opensense_df

sensor_name                        createdAt Luftdruck Temperatur UV-Intensität rel. Luftfeuchte
0           2024-05-20 14:14:28.566000+00:00       NaN      23.66        219.38            48.73
1           2024-05-20 14:15:28.666000+00:00       NaN      23.65        213.75            48.33
2           2024-05-20 14:16:28.843000+00:00       NaN      23.68        213.75            48.33
3           2024-05-20 14:17:28.871000+00:00       NaN      23.72        213.75            48.53
4           2024-05-20 14:18:29.029000+00:00    995.16      23.69           NaN              NaN
...                                      ...       ...        ...           ...              ...
9956        2024-05-27 13:37:49.668000+00:00   1002.67       24.3        348.75            46.97
9957        2024-05-27 13:38:49.791000+00:00   1002.66      24.24        348.75            46.79
9958        2024-05-27 13:39:49.937000+00:00   1002.65      24.18        348.75            46.99
9959        2024-05-27 13:40:50.156000+00:00   1002.63      24.02        348.75            47.19
9960        2024-05-27 13:41:51.083000+00:00   1002.61      24.08        348.75            47.29

[9961 rows x 5 columns]

# Analysen

In [12]:
opensense_df.corr()

sensor_name       createdAt  Luftdruck  Temperatur  UV-Intensität  rel. Luftfeuchte
sensor_name                                                                        
createdAt          1.000000   0.856212    0.247265       0.806908         -0.289728
Luftdruck          0.856212   1.000000    0.037396       0.631213         -0.174472
Temperatur         0.247265   0.037396    1.000000       0.417951         -0.926914
UV-Intensität      0.806908   0.631213    0.417951       1.000000         -0.473599
rel. Luftfeuchte  -0.289728  -0.174472   -0.926914      -0.473599          1.000000

In [13]:
opensense_df.to_csv('sensor_data.csv', index=False)

In [14]:
opensense_df

sensor_name                        createdAt Luftdruck Temperatur UV-Intensität rel. Luftfeuchte
0           2024-05-20 14:14:28.566000+00:00       NaN      23.66        219.38            48.73
1           2024-05-20 14:15:28.666000+00:00       NaN      23.65        213.75            48.33
2           2024-05-20 14:16:28.843000+00:00       NaN      23.68        213.75            48.33
3           2024-05-20 14:17:28.871000+00:00       NaN      23.72        213.75            48.53
4           2024-05-20 14:18:29.029000+00:00    995.16      23.69           NaN              NaN
...                                      ...       ...        ...           ...              ...
9956        2024-05-27 13:37:49.668000+00:00   1002.67       24.3        348.75            46.97
9957        2024-05-27 13:38:49.791000+00:00   1002.66      24.24        348.75            46.79
9958        2024-05-27 13:39:49.937000+00:00   1002.65      24.18        348.75            46.99
9959        2024-05-27 13:40:50.156000+00:00   1002.63      24.02        348.75            47.19
9960        2024-05-27 13:41:51.083000+00:00   1002.61      24.08        348.75            47.29

[9961 rows x 5 columns]

# Resample

# Visualisierung

In [15]:
fig = px.line(opensense_df, x='createdAt', y='Temperatur',title='Temperaturverlauf(°C) über Zeit')

# Achsentitel hinzufügen
fig.update_xaxes(title_text='Messzeitpunkte')
fig.update_yaxes(title_text='Temperatur (°C)')

# Achsenbeschriftungen verbessern
fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')

# Gitterlinien hinzufügen
fig.update_layout(xaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'),
                  yaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'))

# Bildunterschrift unterhalb der Achsenbeschriftungen hinzufügen
fig.update_layout(annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")])

fig.show()


In [16]:
# Temperatur und Luffeuchte
fig = px.line(opensense_df, x='createdAt', y=['Temperatur'], title='Temperatur und Luftfeuchte über Zeit')
fig.add_scatter(x=opensense_df['createdAt'], y=opensense_df['rel. Luftfeuchte'], mode='lines', name='rel. Luftfeuchte', yaxis='y2')

# Achsentitel hinzufügen
fig.update_xaxes(title_text='Messzeitpunkte')
# Achsenbeschriftungen verbessern
fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')


fig.update_layout(yaxis=dict(title='Temperatur (°C)'), yaxis2=dict(title='rel. Luftfeuchte (%)', overlaying='y', side='right'))
fig.update_layout(annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")])
fig.show()

In [17]:
# Temperatur und UV-Index
fig = px.line(opensense_df, x='createdAt', y=['Temperatur'], title='Temperatur und UV-Intensität über Zeit')
fig.add_scatter(x=opensense_df['createdAt'], y=opensense_df['UV-Intensität'], mode='lines', name='UV-Intensität', yaxis='y2')

# Achsentitel hinzufügen
fig.update_xaxes(title_text='Messzeitpunkte')
# Achsenbeschriftungen verbessern
fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')

fig.update_layout(yaxis=dict(title='Temperatur (°C)'), yaxis2=dict(title='UV-Intensität (μW/cm²)', overlaying='y', side='right'))
fig.update_layout(annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")])
fig.show()

In [18]:
# Temperatur und Luffeuchte
fig = px.line(opensense_df, x='createdAt', y=['Luftdruck'], title='Luftdruck und Luftfeuchte über Zeit')
fig.add_scatter(x=opensense_df['createdAt'], y=opensense_df['rel. Luftfeuchte'], mode='lines', name='rel. Luftfeuchte', yaxis='y2')

# Achsentitel hinzufügen
fig.update_xaxes(title_text='Messzeitpunkte')
# Achsenbeschriftungen verbessern
fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')


fig.update_layout(yaxis=dict(title='Luftdruck (hPa)'), yaxis2=dict(title='rel. Luftfeuchte (%)', overlaying='y', side='right'))
fig.update_layout(annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")])
fig.show()

# Dashboard

In [19]:
# import dash
# import dash_core_components as dcc
# import dash_html_components as html
# import dash_bootstrap_components as dbc
# from dash.dependencies import Input, Output
# import plotly.express as px
# import pandas as pd
# import requests

# # Base URL for the OpenSenseMap API
# base_url = "https://api.opensensemap.org/boxes"
# # SenseBox ID
# senseBoxId = "6645db6eeb5aad0007a6e4b6"
# # List of Sensor IDs
# sensorIds = [
#     "6645db6eeb5aad0007a6e4b7",
#     "6645db6eeb5aad0007a6e4b8",
#     "6645db6eeb5aad0007a6e4b9",
#     "6645db6eeb5aad0007a6e4ba"
# ]

# # Parameters
# params = {
#     'format': 'json',
#     'from-date': '2024-05-18T09:00:00Z',
#     'download': 'false',
#     'outliers': 'mark',
#     'outlier-window': 15
# }

# sensor_info = {
#     '6645db6eeb5aad0007a6e4b7': {'name': 'Temperatur', 'unit': '°C'},
#     '6645db6eeb5aad0007a6e4b8': {'name': 'rel. Luftfeuchte', 'unit': '%'},
#     '6645db6eeb5aad0007a6e4b9': {'name': 'Luftdruck', 'unit': 'hPa'},
#     '6645db6eeb5aad0007a6e4ba': {'name': 'UV-Intensität', 'unit': 'μW/cm²'},
# }

# # Function to fetch data from OpenSenseMap API
# def fetch_sensor_data(sensorId):
#     endpoint = f'{base_url}/{senseBoxId}/data/{sensorId}'
#     response = requests.get(endpoint, params=params)
#     if response.status_code == 200:
#         data = response.json()
#         for measurement in data:
#             measurement['Id'] = sensorId
#             measurement['outlier'] = measurement.get('outlier', None)
#         return data
#     else:
#         print(f'Error retrieving data for sensor {sensorId}: {response.status_code}')
#         return []

# # Initialize an empty list to hold the data
# all_data = []

# # Loop through each sensor ID and retrieve data
# for sensorId in sensorIds:
#     all_data.extend(fetch_sensor_data(sensorId))

# # Convert the list of data to a DataFrame
# sense_df = pd.DataFrame(all_data)
# sense_df['createdAt'] = pd.to_datetime(sense_df['createdAt'])
# sense_df['sensor_name'] = sense_df['Id'].map(lambda x: sensor_info[x]['name'])
# sense_df['unit'] = sense_df['Id'].map(lambda x: sensor_info[x]['unit'])

# # Filter out outliers
# sense_df = sense_df[sense_df['outlier'] != True]

# # Pivot the DataFrame for easier plotting
# opensense_df = sense_df.pivot_table(
#     index='createdAt', 
#     columns='sensor_name', 
#     values='value'
# ).reset_index()

# # Anzahl der Messpunkte
# num_measurements = len(sense_df)
# # Anzahl der Fehlerhaften Messungen
# num_outliers = sense_df['isOutlier'].sum()
# # Prozentsatz der Outliers
# percent_outliers = round((num_outliers / num_measurements) * 100,2)


# # Function to create a figure
# def create_figure(df, x, y, title, y_title, y2_title=None):
#     fig = px.line(df, x=x, y=y, title=title)
#     fig.update_xaxes(title_text='Messzeitpunkte')
#     fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')
#     fig.update_layout(
#         xaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'),
#         yaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'),
#         annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")]
#     )
#     if y2_title:
#         fig.add_scatter(x=df[x], y=df[y2_title], mode='lines', name=y2_title, yaxis='y2')
#         fig.update_layout(yaxis=dict(title=y_title), yaxis2=dict(title=y2_title, overlaying='y', side='right'))
#     else:
#         fig.update_yaxes(title_text=y_title)
#     return fig

# # Create the figures
# temp_figure = create_figure(opensense_df, 'createdAt', 'Temperatur', 'Temperaturverlauf (°C) über Zeit', 'Temperatur (°C)')
# temp_humid_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und rel. Luftfeuchte über Zeit', 'Temperatur (°C)', 'rel. Luftfeuchte')
# temp_uv_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und UV-Intensität über Zeit', 'Temperatur (°C)', 'UV-Intensität')
# pressure_humid_figure = create_figure(opensense_df, 'createdAt', ['Luftdruck'], 'Luftdruck und rel. Luftfeuchte über Zeit', 'Luftdruck (hPa)', 'rel. Luftfeuchte')

# # Create the Dash app
# app = dash.Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

# app.layout = html.Div([
#     # Sidebar on the left side
#     html.Div(
#         id='side-panel',
#         style={
#             'width': '25%',  
#             'position': 'fixed',  
#             'top': 0,  # Align to the top
#             'left': 0,  # Align to the left
#             'bottom': 0,  # Align to the bottom
#             'backgroundColor': '#f0f0f0', 
#             'overflowY': 'scroll'  # Enable scrolling if content overflows
#         },
#         children=[
#             html.Div([
#                 html.H2('Umweltmonitoring SS24 Projektarbeit'),
#                 html.P('Im Rahmen eines Fachpraktikums wurde eine OpenSenseBox zur Umweltüberwachung aufgebaut, um Daten wie Luftqualität und Temperatur zu erfassen und zu visualisieren.Die Echtzeitvisualisierung bietet Einblicke in lokale Umweltbedingungen.Ein weiteres Ziel ist die Entwicklung eines Modells zur Wettervorhersage basierend auf diesen Daten'),
#                 # Example image with adjusted size
#                 html.Img(
#                     src='https://docs.sensebox.de/images/2020-10-16-opensensemap-faq/openSenseMap_github.png',
#                     style={
#                         'width': '200px',  
#                         'height': '90px'
#                     }
#                 ),
#                 html.P(f"Anzahl der Messpunkte: {num_measurements}"),
#                 html.P(f"Anzahl der Fehlerhaften Messungen: {num_outliers}"),
#                 html.P(f"Anteil der Fehlerhaften Messungen: {percent_outliers}%"),
#                 html.P("Sensoren:"),
#                 html.Ul([
#                     html.Li(f"{sensor_info[sensor_id]['name']} ({sensor_info[sensor_id]['unit']})")
#                     for sensor_id in sensorIds
#                 ]),
#                 html.P("Beispiel text"),
#             ], style={'padding': '20px'}),
#             html.Footer("Gruppe: Alexandru, Evelyn, Rafael", style={'textAlign': 'left', 'paddingLeft': '20px'})  
#         ]
#     ),
    
#     # Main content on the right side
#     html.Div([
#         dbc.Container([
#             dbc.Row([
#                 dbc.Col(dcc.Graph(figure=temp_figure), width=6),
#                 dbc.Col(dcc.Graph(figure=temp_humid_figure), width=6)
#             ]),
#             dbc.Row([
#                 dbc.Col(dcc.Graph(figure=temp_uv_figure), width=6),
#                 dbc.Col(dcc.Graph(figure=pressure_humid_figure), width=6)
#             ])
#         ], fluid=True)
#     ], style={'marginLeft': '25%', 'padding': '10px'})  # Adjust left margin to make space for the sidebar
# ])

# if __name__ == '__main__':
#     app.run_server(debug=True)


# App callback automatische aktualisierung

In [20]:
import dash
from dash import dcc
from dash import html
import dash_bootstrap_components as dbc
from dash.dependencies import Input, Output
import plotly.express as px
import pandas as pd
import requests

# Base URL for the OpenSenseMap API
base_url = "https://api.opensensemap.org/boxes"
# SenseBox ID
senseBoxId = "6645db6eeb5aad0007a6e4b6"
# List of Sensor IDs
sensorIds = [
    "6645db6eeb5aad0007a6e4b7",
    "6645db6eeb5aad0007a6e4b8",
    "6645db6eeb5aad0007a6e4b9",
    "6645db6eeb5aad0007a6e4ba"
]

# Parameters
params = {
    'format': 'json',
    'from-date': '2024-05-18T09:00:00Z',
    'download': 'false',
    'outliers': 'mark',
    'outlier-window': 15
}

sensor_info = {
    '6645db6eeb5aad0007a6e4b7': {'name': 'Temperatur', 'unit': '°C'},
    '6645db6eeb5aad0007a6e4b8': {'name': 'rel. Luftfeuchte', 'unit': '%'},
    '6645db6eeb5aad0007a6e4b9': {'name': 'Luftdruck', 'unit': 'hPa'},
    '6645db6eeb5aad0007a6e4ba': {'name': 'UV-Intensität', 'unit': 'μW/cm²'},
}

# Function to fetch data from OpenSenseMap API
def fetch_sensor_data(sensorId):
    endpoint = f'{base_url}/{senseBoxId}/data/{sensorId}'
    response = requests.get(endpoint, params=params)
    if response.status_code == 200:
        data = response.json()
        for measurement in data:
            measurement['Id'] = sensorId
            measurement['outlier'] = measurement.get('outlier', None)
        return data
    else:
        print(f'Error retrieving data for sensor {sensorId}: {response.status_code}')
        return []

# Initialize an empty list to hold the data
all_data = []

# Loop through each sensor ID and retrieve data
for sensorId in sensorIds:
    all_data.extend(fetch_sensor_data(sensorId))

# Convert the list of data to a DataFrame
sense_df = pd.DataFrame(all_data)
sense_df['createdAt'] = pd.to_datetime(sense_df['createdAt'])
sense_df['sensor_name'] = sense_df['Id'].map(lambda x: sensor_info[x]['name'])
sense_df['unit'] = sense_df['Id'].map(lambda x: sensor_info[x]['unit'])

# Filter out outliers
sense_df = sense_df[sense_df['outlier'] != True]

# Pivot the DataFrame for easier plotting
opensense_df = sense_df.pivot_table(
    index='createdAt', 
    columns='sensor_name', 
    values='value'
).reset_index()

# Anzahl der Messpunkte
num_measurements = len(sense_df)
# Anzahl der Fehlerhaften Messungen
num_outliers = sense_df['outlier'].sum()
# Prozentsatz der Outliers
percent_outliers = round((num_outliers / num_measurements) * 100, 2)

# Function to create a figure
def create_figure(df, x, y, title, y_title, y2_title=None):
    fig = px.line(df, x=x, y=y, title=title)
    fig.update_xaxes(title_text='Messzeitpunkte')
    fig.update_xaxes(tickangle=45, tickformat='%Y-%m-%d')
    fig.update_layout(
        xaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'),
        yaxis=dict(showgrid=True, gridwidth=1, gridcolor='LightGrey'),
        annotations=[dict(xref='paper', yref='paper', x=0.5, y=0.0, showarrow=False, text="Hinweis: Ausreißer wurden entfernt")]
    )
    if y2_title:
        fig.add_scatter(x=df[x], y=df[y2_title], mode='lines', name=y2_title, yaxis='y2')
        fig.update_layout(yaxis=dict(title=y_title), yaxis2=dict(title=y2_title, overlaying='y', side='right'))
    else:
        fig.update_yaxes(title_text=y_title)
    return fig

# Create the figures
temp_figure = create_figure(opensense_df, 'createdAt', 'Temperatur', 'Temperaturverlauf (°C) über Zeit', 'Temperatur (°C)')
temp_humid_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und rel. Luftfeuchte über Zeit', 'Temperatur (°C)', 'rel. Luftfeuchte')
temp_uv_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und UV-Intensität über Zeit', 'Temperatur (°C)', 'UV-Intensität')
pressure_humid_figure = create_figure(opensense_df, 'createdAt', ['Luftdruck'], 'Luftdruck und rel. Luftfeuchte über Zeit', 'Luftdruck (hPa)', 'rel. Luftfeuchte')

# Create the Dash app
app = dash.Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

# Layout definition
app.layout = html.Div([
    # Sidebar on the left side
    html.Div(
        id='side-panel',
        style={
            'width': '25%',  
            'position': 'fixed',  
            'top': 0,  
            'left': 0,  
            'bottom': 0,  
            'backgroundColor': '#f0f0f0', 
            'overflowY': 'scroll'  
        },
        children=[
            html.Div([
                html.H2('Umweltmonitoring SS24 Projektarbeit'),
                html.P('Im Rahmen eines Fachpraktikums wurde eine OpenSenseBox zur Umweltüberwachung aufgebaut, um Daten wie Luftqualität und Temperatur zu erfassen und zu visualisieren. Die Echtzeitvisualisierung bietet Einblicke in lokale Umweltbedingungen. Ein weiteres Ziel ist die Entwicklung eines Modells zur Wettervorhersage basierend auf diesen Daten.'),
                html.Img(
                    src='https://docs.sensebox.de/images/2020-10-16-opensensemap-faq/openSenseMap_github.png',
                    style={
                        'width': '200px',  
                        'height': '90px'
                    }
                ),
                html.P(f"Anzahl der Messpunkte: {num_measurements}"),
                html.P(f"Anzahl der Fehlerhaften Messungen: {num_outliers}"),
                html.P(f"Anteil der Fehlerhaften Messungen: {percent_outliers}%"),
                html.P("Sensoren:"),
                html.Ul([
                    html.Li(f"{sensor_info[sensor_id]['name']} ({sensor_info[sensor_id]['unit']})")
                    for sensor_id in sensorIds
                ]),
                html.P("Beispiel text"),
            ], style={'padding': '20px'}),
            html.Footer("Gruppe: Alexandru, Evelyn, Rafael", style={'textAlign': 'left', 'paddingLeft': '20px'})  
        ]
    ),
    
    # Main content on the right side
    html.Div([
        dbc.Container([
            dbc.Row([
                dbc.Col(dcc.Graph(id='temp-figure', figure=temp_figure), width=6),
                dbc.Col(dcc.Graph(id='temp-humid-figure', figure=temp_humid_figure), width=6)
            ]),
            dbc.Row([
                dbc.Col(dcc.Graph(id='temp-uv-figure', figure=temp_uv_figure), width=6),
                dbc.Col(dcc.Graph(id='pressure-humid-figure', figure=pressure_humid_figure), width=6)
            ])
        ], fluid=True)
    ], style={'marginLeft': '25%', 'padding': '10px'})  
])

# Interval component for auto-updating the graphs
interval = dcc.Interval(id='interval-component', interval=60_000, n_intervals=0)

# Add interval component to the layout
app.layout.children.append(interval)

# Callback function to update the figures
@app.callback(
    [Output('temp-figure', 'figure'),
     Output('temp-humid-figure', 'figure'),
     Output('temp-uv-figure', 'figure'),
     Output('pressure-humid-figure', 'figure')],
    [Input('interval-component', 'n_intervals')]
)
def update_figures(n_intervals):
    all_data = []
    for sensorId in sensorIds:
        all_data.extend(fetch_sensor_data(sensorId))

    sense_df = pd.DataFrame(all_data)
    sense_df['createdAt'] = pd.to_datetime(sense_df['createdAt'])
    sense_df['sensor_name'] = sense_df['Id'].map(lambda x: sensor_info[x]['name'])
    sense_df['unit'] = sense_df['Id'].map(lambda x: sensor_info[x]['unit'])

    sense_df = sense_df[sense_df['outlier'] != True]

    opensense_df = sense_df.pivot_table(
        index='createdAt',
        columns='sensor_name',
        values='value'
    ).reset_index()

    temp_figure = create_figure(opensense_df, 'createdAt', 'Temperatur', 'Temperaturverlauf (°C) über Zeit', 'Temperatur (°C)')
    temp_humid_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und rel. Luftfeuchte über Zeit', 'Temperatur (°C)', 'rel. Luftfeuchte')
    temp_uv_figure = create_figure(opensense_df, 'createdAt', ['Temperatur'], 'Temperatur und UV-Intensität über Zeit', 'Temperatur (°C)', 'UV-Intensität')
    pressure_humid_figure = create_figure(opensense_df, 'createdAt', ['Luftdruck'], 'Luftdruck und rel. Luftfeuchte über Zeit', 'Luftdruck (hPa)', 'rel. Luftfeuchte')

    return temp_figure, temp_humid_figure, temp_uv_figure, pressure_humid_figure

if __name__ == '__main__':
    app.run_server(debug=True)


# Datenbankverbidnung

In [ ]:
import requests
import pandas as pd
import psycopg2
from datetime import datetime

# Datenbankverbindung herstellen
conn = psycopg2.connect(
    dbname="sense_data",
    user="postgres",
    password="test",  
    host="localhost"
)
cur = conn.cursor()

# Base URL für die OpenSenseMap API
base_url = "https://api.opensensemap.org/boxes"
senseBoxId = "6645db6eeb5aad0007a6e4b6"
sensorIds = [
    "6645db6eeb5aad0007a6e4b7",
    "6645db6eeb5aad0007a6e4b8",
    "6645db6eeb5aad0007a6e4b9",
    "6645db6eeb5aad0007a6e4ba"
]

params = {
    'format': 'json',
    'from-date': '2024-05-18T09:00:00Z',
    'download': 'true',
    'outliers': 'mark',
    'outlier-window': 15,
    'delimiter': 'comma'
}

sensor_info = {
    '6645db6eeb5aad0007a6e4b7': {'name': 'Temperatur', 'unit': '°C'},
    '6645db6eeb5aad0007a6e4b8': {'name': 'rel. Luftfeuchte', 'unit': '%'},
    '6645db6eeb5aad0007a6e4b9': {'name': 'Luftdruck', 'unit': 'hPa'},
    '6645db6eeb5aad0007a6e4ba': {'name': 'UV-Intensität', 'unit': 'μW/cm²'},
}

# Daten abrufen und in die Datenbank importieren
for sensorId in sensorIds:
    endpoint = f'{base_url}/{senseBoxId}/data/{sensorId}'
    response = requests.get(endpoint, params=params)
    if response.status_code == 200:
        data = response.json()
        for measurement in data:
            created_at = measurement['createdAt']
            value = measurement['value']
            outlier = measurement.get('outlier', None)
            sensor_name = sensor_info[sensorId]['name']
            unit = sensor_info[sensorId]['unit']
            # Hier fügen Sie die Geometrie hinzu (z.B. den Standort der SenseBox, dies ist ein Beispielwert)
            geom = 'SRID=4326;POINT(7.6285 51.9607)'  # Ersetzen Sie longitude und latitude durch tatsächliche Werte
            
            # SQL-Befehl zum Einfügen der Daten
            insert_query = """
                INSERT INTO sensor_data (sensor_id, created_at, value, outlier, sensor_name, unit, geom)
                VALUES (%s, %s, %s, %s, %s, %s, ST_GeogFromText(%s));
            """
            cur.execute(insert_query, (sensorId, created_at, value, outlier, sensor_name, unit, geom))

conn.commit()
cur.close()
conn.close()


In [ ]:
# Verbindung zur Datenbank herstellen
conn = psycopg2.connect(
    dbname="sense_data",
    user="postgres",
    password="test",
    host="localhost"
)

# Cursor erstellen
cur = conn.cursor()

# SQL-Abfrage definieren
sql_query = "SELECT * FROM sensor_data WHERE sensor_id = %s;"

# Parameter für die Abfrage
sensor_id = '6645db6eeb5aad0007a6e4b7'

# Abfrage ausführen
cur.execute(sql_query, (sensor_id,))

# Ergebnisse abrufen
results = cur.fetchall()

# Ergebnisse anzeigen
for row in results:
    print(row)

# Cursor und Verbindung schließen
cur.close()
conn.close()

(1, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 29, 12, 598000), 17.48, None, 'Temperatur', '°C', '0101000020E6100000DD24068195831E4034A2B437F8FA4940')
(2, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 28, 12, 510000), 17.55, None, 'Temperatur', '°C', '0101000020E6100000DD24068195831E4034A2B437F8FA4940')
(3, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 27, 12, 371000), 17.7, None, 'Temperatur', '°C', '0101000020E6100000DD24068195831E4034A2B437F8FA4940')
(4, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 26, 12, 211000), 17.62, None, 'Temperatur', '°C', '0101000020E6100000DD24068195831E4034A2B437F8FA4940')
(5, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 25, 12, 182000), 17.77, None, 'Temperatur', '°C', '0101000020E6100000DD24068195831E4034A2B437F8FA4940')
(6, '6645db6eeb5aad0007a6e4b7', datetime.datetime(2024, 5, 21, 13, 24, 12, 147000), 17.77, None, 'Temperatur', '°C', '0101000020E6100000DD24068195

In [ ]:
conn = psycopg2.connect(
    dbname="sense_data",
    user="postgres",
    password="test",
    host="localhost"
)
query = "SELECT * FROM sensor_data;"
df = pd.read_sql_query(query, conn)

fig = px.scatter(df, x='created_at', y='value', color='sensor_name', title='Sensor Data over Time')
fig.show()


/var/folders/hl/g54whv_j0vd21tv5fjmrvw6m0000gn/T/ipykernel_71083/1681874281.py:8: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



# Modell

In [ ]:
import requests
import pandas as pd
from datetime import datetime

# Base URL for the OpenSenseMap API
base_url = "https://api.opensensemap.org/boxes"
# SenseBox ID
senseBoxId = "6645db6eeb5aad0007a6e4b6"
# List of Sensor IDs
sensorIds = [
    "6645db6eeb5aad0007a6e4b7",  
    "6645db6eeb5aad0007a6e4b8",
    "6645db6eeb5aad0007a6e4b9",
    "6645db6eeb5aad0007a6e4ba"
]

# Parameters
params = {
    'format': 'json',            
    'from-date': '2024-05-16T19:00:00Z',
    'to-date': datetime.now().isoformat() + 'Z',  # Ensure proper formatting and timezone
    'download': 'true',          
    'outliers': 'mark',          
    'outlier-window': 15,        
    'delimiter': 'comma'         
}

all_data = []

for sensorId in sensorIds:
    endpoint = f'{base_url}/{senseBoxId}/data/{sensorId}'
    response = requests.get(endpoint, params=params)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        # Add sensor ID to each measurement
        for measurement in data:
            measurement['Id'] = sensorId
            # Check for outliers and add an 'outlier' column
            if 'outlier' in measurement:
                measurement['outlier'] = measurement['outlier']
            else:
                measurement['outlier'] = None  # If no outlier info, set as None
        all_data.extend(data)
    else:
        print(f'Error retrieving data for sensor {sensorId}: {response.status_code}')

# Convert to DataFrame
sense_df = pd.DataFrame(all_data)

# Check if the DataFrame is not empty and sort by 'createdAt' to get the latest measurements
if not sense_df.empty:
    sense_df = sense_df.sort_values(by='createdAt', ascending=False)



location                 createdAt   value  isOutlier                        Id outlier
27771  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z    0.00      False  6645db6eeb5aad0007a6e4ba    None
20828  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z  990.80      False  6645db6eeb5aad0007a6e4b9    None
13885  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z   65.93      False  6645db6eeb5aad0007a6e4b8    None
6942   [8.410042, 49.001548]  2024-05-16T19:00:44.913Z   18.73       True  6645db6eeb5aad0007a6e4b7    None
6941   [8.410042, 49.001548]  2024-05-16T19:01:44.973Z   18.65      False  6645db6eeb5aad0007a6e4b7    None
...                      ...                       ...     ...        ...                       ...     ...
20830  [8.410042, 49.001548]  2024-05-21T15:17:25.107Z  213.75      False  6645db6eeb5aad0007a6e4ba    None
13886  [8.410042, 49.001548]  2024-05-21T15:18:25.228Z  993.92      False  6645db6eeb5aad0007a6e4b9    None
20829  [8.410042, 49.001548]  2024-05-21T15:18:25.228Z  208.12      False  6645db6eeb5aad0007a6e4ba    None
6943   [8.410042, 49.001548]  2024-05-21T15:18:25.228Z   79.05      False  6645db6eeb5aad0007a6e4b8    None
0      [8.410042, 49.001548]  2024-05-21T15:18:25.228Z   18.57      False  6645db6eeb5aad0007a6e4b7    None

[27772 rows x 6 columns]

In [ ]:
sense_df.sort_values(by ='createdAt', ascending = False)

location                 createdAt   value  isOutlier                        Id outlier
0      [8.410042, 49.001548]  2024-05-21T15:18:25.228Z   18.57      False  6645db6eeb5aad0007a6e4b7    None
13886  [8.410042, 49.001548]  2024-05-21T15:18:25.228Z  993.92      False  6645db6eeb5aad0007a6e4b9    None
6943   [8.410042, 49.001548]  2024-05-21T15:18:25.228Z   79.05      False  6645db6eeb5aad0007a6e4b8    None
20829  [8.410042, 49.001548]  2024-05-21T15:18:25.228Z  208.12      False  6645db6eeb5aad0007a6e4ba    None
1      [8.410042, 49.001548]  2024-05-21T15:17:25.107Z   18.21      False  6645db6eeb5aad0007a6e4b7    None
...                      ...                       ...     ...        ...                       ...     ...
27770  [8.410042, 49.001548]  2024-05-16T19:01:44.973Z    0.00      False  6645db6eeb5aad0007a6e4ba    None
20828  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z  990.80      False  6645db6eeb5aad0007a6e4b9    None
6942   [8.410042, 49.001548]  2024-05-16T19:00:44.913Z   18.73       True  6645db6eeb5aad0007a6e4b7    None
13885  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z   65.93      False  6645db6eeb5aad0007a6e4b8    None
27771  [8.410042, 49.001548]  2024-05-16T19:00:44.913Z    0.00      False  6645db6eeb5aad0007a6e4ba    None

[27772 rows x 6 columns]

In [ ]:
import requests

# ID der OpenSenseBox
box_id = '6645db6eeb5aad0007a6e4b6'

# URL zur API
url = f"https://api.opensensemap.org/boxes/{box_id}"

# GET-Anfrage an die API
response = requests.get(url)

# Überprüfung der Antwort
if response.status_code == 200:
    data = response.json()
    if 'sensors' in data:
        for sensor in data['sensors']:
            print(sensor)
            if sensor['title'] == 'Temperatur':
                temperature = sensor['lastMeasurement']['value']
                print("Aktuelle Temperatur:", temperature)
                break
    else:
        print("Keine Sensordaten gefunden.")
else:
    print(f"Fehler beim Abrufen der Daten: {response.status_code}")


{'_id': '6645db6eeb5aad0007a6e4b7', 'icon': 'osem-thermometer', 'title': 'Temperatur', 'unit': '°C', 'sensorType': 'HDC1080', 'lastMeasurement': {'createdAt': '2024-05-21T15:26:26.103Z', 'value': '18.44'}}
Aktuelle Temperatur: 18.44


In [ ]:
url

'https://api.opensensemap.org/boxes/6645db6eeb5aad0007a6e4b6'

In [ ]:
data

{'_id': '6645db6eeb5aad0007a6e4b6',
 'grouptag': ['edu'],
 'model': 'custom',
 'name': 'Pferdestall',
 'currentLocation': {'type': 'Point',
  'coordinates': [8.410042, 49.001548],
  'timestamp': '2024-05-16T10:09:50.187Z'},
 'exposure': 'outdoor',
 'sensors': [{'_id': '6645db6eeb5aad0007a6e4b7',
   'icon': 'osem-thermometer',
   'title': 'Temperatur',
   'unit': '°C',
   'sensorType': 'HDC1080',
   'lastMeasurement': {'createdAt': '2024-05-21T15:26:26.103Z',
    'value': '18.44'}},
  {'_id': '6645db6eeb5aad0007a6e4b8',
   'icon': 'osem-humidity',
   'title': 'rel. Luftfeuchte',
   'unit': '%',
   'sensorType': 'HDC1080',
   'lastMeasurement': {'createdAt': '2024-05-21T15:26:26.103Z',
    'value': '77.08'}},
  {'_id': '6645db6eeb5aad0007a6e4b9',
   'icon': 'osem-barometer',
   'title': 'Luftdruck',
   'unit': 'hPa',
   'sensorType': 'DPS310',
   'lastMeasurement': {'createdAt': '2024-05-21T15:26:26.103Z',
    'value': '993.90'}},
  {'_id': '6645db6eeb5aad0007a6e4ba',
   'icon': 'osem-br

In [ ]:
temperature

'18.39'